# Topic Modeling

This notebook wants to explore the topic modeling possibilities of the summaries dataset. We will implement the model using Bertopic.

In [1]:
# Modules to import
import sys
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import seaborn as sns

In [2]:
paths = ['../data','../scripts','../utils']
for path in paths:
    sys.path.append(path)

In [3]:
from dataLoader import loadDataframe

In [4]:
# Load data
path_to_directory = '../../data/cleanData/'
df_movies = loadDataframe('movies', path_to_directory)
df_summaries = loadDataframe('summaries', path_to_directory)

c:\Users\arnau\OneDrive\Documents\Scolarité EPFL\ADA\ada-2024-project-teamcsx24\src\models\../data\dataLoader.py:10: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df[columns_to_convert] = df[columns_to_convert].applymap(eval)


### Bertopic

In [5]:
import spacy
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
import string
from tqdm import tqdm

In [6]:
# Load the spaCy model for English language
nlp = spacy.load("en_core_web_sm")

# Download stopwords and punkt tokenizer
import nltk
nltk.download('stopwords')
nltk.download('punkt')

# Load the English stopwords
stop_words = set(stopwords.words("english"))

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\arnau\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\arnau\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [7]:
def preprocess_text(text):
    # Tokenisation
    doc = nlp(text.lower())  # Convert to lowercase
    
    # Lemmatisation and remove stopwords and punctuation
    processed_tokens = [
        token.lemma_ for token in doc if token.text not in stop_words and token.text not in string.punctuation
    ]
    
    char_to_remove = ["'s", " "]
    processed_tokens = [token for token in processed_tokens if token not in char_to_remove]
    
    return " ".join(processed_tokens)

In [8]:
df_summaries.head()

wiki_id                                            summary
0  23890098  Shlykov, a hard-working taxi driver and Lyosha...
1  31186339  The nation of Panem consists of a wealthy Capi...
2  20663735  Poovalli Induchoodan  is sentenced for six yea...
3   2231378  The Lemon Drop Kid , a New York City swindler,...
4    595909  Seventh-day Adventist Church pastor Michael Ch...

In [ ]:
# Apply the preprocessing to the summaries
tqdm.pandas()
df_cleaned_summaries = df_summaries.copy()
df_cleaned_summaries["cleaned_summary"] = df_cleaned_summaries["summary"].progress_apply(preprocess_text)

# Drop the original summary column
df_cleaned_summaries.drop(columns=["summary"], inplace=True)

  0%|          | 0/42303 [00:00<?, ?it/s]

100%|██████████| 42303/42303 [39:01<00:00, 18.07it/s]  


All the summaries are not in English, so we use the library `langdetect` to filter out the non-English summaries.

In [25]:
# Reconnaitre la langue de chaque summary
from langdetect import detect

def detect_language(text):
    try:
        return detect(text)
    except:
        return "unknown"

df_cleaned_summaries["language"] = df_cleaned_summaries["cleaned_summary"].progress_apply(detect_language)

100%|██████████| 42303/42303 [06:38<00:00, 106.04it/s]


In [11]:
# Save the cleaned summaries
df_cleaned_summaries.to_csv("../../data/topicModelData/cleaned_summaries.csv", index=False)

In [12]:
pourcentage_english = df_cleaned_summaries["language"].value_counts(normalize=True)["en"] * 100
print('Pourcentage of summaries in English: {:.2f}%'.format(pourcentage_english))

Pourcentage of summaries in English: 99.53%


In [10]:
df_cleaned_summaries = pd.read_csv("../../data/topicModelData/cleaned_summaries.csv")

We can just decide to drop the non-English summaries or translate them to English. In this notebook, we will drop the non-English summaries.

In [13]:
df_cleaned_summaries = df_cleaned_summaries[df_cleaned_summaries["language"] == "en"]

In [14]:
from bertopic import BERTopic
from sentence_transformers import SentenceTransformer

c:\Users\arnau\anaconda3\envs\ada\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [15]:
# Embedding model
embedding_model = SentenceTransformer("all-MiniLM-L6-v2")

# Encode the summaries
embeddings = embedding_model.encode(df_cleaned_summaries['cleaned_summary'].tolist(), show_progress_bar=True)

Batches: 100%|██████████| 1316/1316 [40:26<00:00,  1.84s/it] 


In [16]:
# Create the model
topic_model = BERTopic(embedding_model=embedding_model, verbose=True)

# Fit the model
topics, probabilities = topic_model.fit_transform(df_cleaned_summaries['cleaned_summary'].tolist())
df_cleaned_summaries['topic'] = topics

2024-11-24 10:57:02,619 - BERTopic - Embedding - Transforming documents to embeddings.
Batches: 100%|██████████| 1316/1316 [39:33<00:00,  1.80s/it] 
2024-11-24 11:36:39,906 - BERTopic - Embedding - Completed ✓
2024-11-24 11:36:39,906 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
2024-11-24 11:37:35,978 - BERTopic - Dimensionality - Completed ✓
2024-11-24 11:37:35,989 - BERTopic - Cluster - Start clustering the reduced embeddings
2024-11-24 11:37:46,514 - BERTopic - Cluster - Completed ✓
2024-11-24 11:37:46,537 - BERTopic - Representation - Extracting topics from clusters using representation models.
2024-11-24 11:37:54,297 - BERTopic - Representation - Completed ✓


In [17]:
# Print the topics
topic_info = topic_model.get_topic_info()
print(topic_info)

     Topic  Count                                 Name  \
0       -1  25994                  -1_find_go_take_get   
1        0   1321                      0_ho_su_li_wong   
2        1   1200          1_mother_husband_year_child   
3        2    921               2_love_marry_singh_get   
4        3    897       3_murder_bank_detective_prison   
..     ...    ...                                  ...   
222    221     10    221_luther_halligan_brewster_jöns   
223    222     10      222_molly_lasch_dwayne_danielle   
224    223     10     223_japanese_chinese_troop_ahmad   
225    224     10  224_bardot_vadim_merteuil_madeleine   
226    225     10        225_pelikán_dato_dániel_zoran   

                                        Representation  \
0    [find, go, take, get, one, leave, tell, man, f...   
1    [ho, su, li, wong, jin, hong, master, eun, chi...   
2    [mother, husband, year, child, life, father, f...   
3    [love, marry, singh, get, father, raja, marria...   
4    [murder,

Our algorithm provides 227 different topics. We have to explore the topics to understand if they make sense and if some are redundant or useless.

In [18]:
# Visualise topics by dominant words
topic_model.visualize_barchart()

ValueError: Mime type rendering requires nbformat>=4.2.0 but it is not installed

Figure({
    'data': [{'marker': {'color': '#D55E00'},
              'orientation': 'h',
              'type': 'bar',
              'x': [0.006696581837555884, 0.006827189071461151,
                    0.00777077824645047, 0.008816023134916856,
                    0.009026522353271468],
              'xaxis': 'x',
              'y': [jin  , wong  , li  , su  , ho  ],
              'yaxis': 'y'},
             {'marker': {'color': '#0072B2'},
              'orientation': 'h',
              'type': 'bar',
              'x': [0.005907433206915955, 0.005977149772123236,
                    0.006443824878492132, 0.006789510161704263,
                    0.007567609392077789],
              'xaxis': 'x2',
              'y': [life  , child  , year  , husband  , mother  ],
              'yaxis': 'y2'},
             {'marker': {'color': '#CC79A7'},
              'orientation': 'h',
              'type': 'bar',
              'x': [0.0052443273667025095, 0.005268356400070142,
                    0.005592118230729149, 0.0057740725710867516,
                    0.006258377112465603],
              'xaxis': 'x3',
              'y': [father  , get  , singh  , marry  , love  ],
              'yaxis': 'y3'},
             {'marker': {'color': '#E69F00'},
              'orientation': 'h',
              'type': 'bar',
              'x': [0.008414541265023941, 0.00882365074253823,
                    0.00911966333289485, 0.00978082782306575, 0.010847405979250248],
              'xaxis': 'x4',
              'y': [crime  , prison  , detective  , bank  , murder  ],
              'yaxis': 'y4'},
             {'marker': {'color': '#56B4E9'},
              'orientation': 'h',
              'type': 'bar',
              'x': [0.007518723445415273, 0.008021525305329447,
                    0.008483417550258818, 0.009100780500289386,
                    0.020732324552750002],
              'xaxis': 'x5',
              'y': [character  , com  , story  , movie  , film  ],
              'yaxis': 'y5'},
             {'marker': {'color': '#009E73'},
              'orientation': 'h',
              'type': 'bar',
              'x': [0.010172724551463114, 0.010594032651056053,
                    0.012087592186636917, 0.012429880100963893,
                    0.015381463782484438],
              'xaxis': 'x6',
              'y': [daughter  , family  , love  , marriage  , marry  ],
              'yaxis': 'y6'},
             {'marker': {'color': '#F0E442'},
              'orientation': 'h',
              'type': 'bar',
              'x': [0.005510678056615773, 0.005536425319816836,
                    0.005716424183311392, 0.007625075213291968,
                    0.009090466916712725],
              'xaxis': 'x7',
              'y': [detective  , shoot  , kill  , police  , frank  ],
              'yaxis': 'y7'},
             {'marker': {'color': '#D55E00'},
              'orientation': 'h',
              'type': 'bar',
              'x': [0.005672715909266816, 0.006594013439037318,
                    0.007869075568660648, 0.009698021985908144,
                    0.013399229855452277],
              'xaxis': 'x8',
              'y': [girl  , prom  , hannah  , student  , school  ],
              'yaxis': 'y8'}],
    'layout': {'annotations': [{'font': {'size': 16},
                                'showarrow': False,
                                'text': 'Topic 0',
                                'x': 0.0875,
                                'xanchor': 'center',
                                'xref': 'paper',
                                'y': 1.0,
                                'yanchor': 'bottom',
                                'yref': 'paper'},
                               {'font': {'size': 16},
                                'showarrow': False,
                                'text': 'Topic 1',
                                'x': 0.36250000000000004,
                                'xanchor': 'center',
                                'xref': 'paper',
   

In [19]:
# Visualise topics on a map
topic_model.visualize_topics()

ValueError: Mime type rendering requires nbformat>=4.2.0 but it is not installed

Figure({
    'data': [{'customdata': array([[0, 'ho | su | li | wong | jin', 1321],
                                   [1, 'mother | husband | year | child | life', 1200],
                                   [2, 'love | marry | singh | get | father', 921],
                                   ...,
                                   [223, 'japanese | chinese | troop | ahmad | wheeler', 10],
                                   [224, 'bardot | vadim | merteuil | madeleine | valmont', 10],
                                   [225, 'pelikán | dato | dániel | zoran | communist', 10]], dtype=object),
              'hovertemplate': '<b>Topic %{customdata[0]}</b><br>%{customdata[1]}<br>Size: %{customdata[2]}',
              'legendgroup': '',
              'marker': {'color': '#B0BEC5',
                         'line': {'color': 'DarkSlateGrey', 'width': 2},
                         'size': array([1321, 1200,  921, ...,   10,   10,   10]),
                         'sizemode': 'area',
                         'sizeref': np.float64(0.825625),
                         'symbol': 'circle'},
              'mode': 'markers',
              'name': '',
              'orientation': 'v',
              'showlegend': False,
              'type': 'scatter',
              'x': array([-0.5613595 ,  6.976317  , -1.8064177 , ..., 12.089937  , -4.9060054 ,
                          -0.02310647], dtype=float32),
              'xaxis': 'x',
              'y': array([ 3.958769 , -2.6162932, 12.626923 , ...,  2.8645358,  3.7202654,
                           2.0243065], dtype=float32),
              'yaxis': 'y'}],
    'layout': {'annotations': [{'showarrow': False,
                                'text': 'D1',
                                'x': np.float32(-11.823822),
                                'y': np.float32(8.220751),
                                'yshift': 10},
                               {'showarrow': False,
                                'text': 'D2',
                                'x': np.float32(6.5131607),
                                'xshift': 10,
                                'y': np.float32(27.530249)}],
               'height': 650,
               'hoverlabel': {'bgcolor': 'white', 'font': {'family': 'Rockwell', 'size': 16}},
               'legend': {'itemsizing': 'constant', 'tracegroupgap': 0},
               'margin': {'t': 60},
               'shapes': [{'line': {'color': '#CFD8DC', 'width': 2},
                           'type': 'line',
                           'x0': np.float32(6.5131607),
                           'x1': np.float32(6.5131607),
                           'y0': np.float32(-11.088747),
                           'y1': np.float32(27.530249)},
                          {'line': {'color': '#9E9E9E', 'width': 2},
                           'type': 'line',
                           'x0': np.float32(-11.823822),
                           'x1': np.float32(24.850143),
                           'y0': np.float32(8.220751),
                           'y1': np.float32(8.220751)}],
               'sliders': [{'active': 0,
                            'pad': {'t': 50},
                            'steps': [{'args': [{'marker.color': [['red',
                                                                  '#B0BEC5',
                                                                  '#B0BEC5',
                                                                  '#B0BEC5',
                                                                  '#B0BEC5',
                                                                  '#B0BEC5',
                                                                  '#B0BEC5',
                                                                  '#B0BEC5',
                                                                  '#B0BEC5',
                                                                  '#B0BEC5',
                                                                  '#B0BEC5',
                       

In [20]:
# Save the model
topic_model.save("topic_model")

2024-11-24 12:15:51,684 - BERTopic - WARNING: When you use `pickle` to save/load a BERTopic model,please make sure that the environments in which you saveand load the model are **exactly** the same. The version of BERTopic,its dependencies, and python need to remain the same.


In [21]:
# Save the topics
df_cleaned_summaries.to_csv("../../data/topicModelData/summaries_with_topics.csv", index=False)

### Review topics

Merge similar topics

Drop non-informative topics

In [57]:
topic_info.head()

Topic  Count                            Name  \
0     -1  25994             -1_find_go_take_get   
1      0   1321                 0_ho_su_li_wong   
2      1   1200     1_mother_husband_year_child   
3      2    921          2_love_marry_singh_get   
4      3    897  3_murder_bank_detective_prison   

                                      Representation  \
0  [find, go, take, get, one, leave, tell, man, f...   
1  [ho, su, li, wong, jin, hong, master, eun, chi...   
2  [mother, husband, year, child, life, father, f...   
3  [love, marry, singh, get, father, raja, marria...   
4  [murder, bank, detective, prison, crime, polic...   

                                 Representative_Docs  
0  [babel focus four interrelated set situation c...  
1  [leader kong tung clan yen chan ying ruthless ...  
2  [david catherine robinson move rundown country...  
3  [story focusse three character different persp...  
4  [three outlaws rob bank one wound two partner ...

In [63]:
docs = df_cleaned_summaries['cleaned_summary'].tolist()
topic_distr, _ = topic_model.approximate_distribution(docs)

100%|██████████| 43/43 [02:01<00:00,  2.83s/it]


### Analysis using df_movies